In [0]:
from pyspark.sql.types import IntegerType
#from pyspark.sql.functions import translate, upper
from pyspark.sql.functions import *
from datetime import datetime

In [0]:
%sql
select upper(LOCATION), count(*) from bronze.conflito where UPPER(LOCATION) like '%ZONE%' group by LOCATION order by LOCATION 

upper(LOCATION) count(1) RIO DE JANEIRO - CENTRAL ZONE 926 RIO DE JANEIRO - NORTH ZONE 3038 RIO DE JANEIRO - SOUTH ZONE 590 RIO DE JANEIRO - WEST ZONE 1859 SAO PAULO - CENTRAL ZONE 476 SAO PAULO - EAST ZONE 271 SAO PAULO - NORTH ZONE 172 SAO PAULO - SOUTH ZONE 422 SAO PAULO - WEST ZONE 179

In [0]:
## carregando os dados do DATABASE bronze para tratamento dos dados de Conflito

df_conflito_bronze_sql = spark.sql('''select * from bronze.conflito''')

print("TABELA CONFLITO CARREGADA COM SUCESSO DO DATABASE BRONZE!")

TABELA CONFLITO CARREGADA COM SUCESSO DO DATABASE BRONZE!


In [0]:
## carregando os dados do DATABASE bronze para tratamento dos dados de Cidade

df_cidade_bronze_sql = spark.sql('''select * from bronze.cidade''')

print("TABELA CIDADE CARREGADA COM SUCESSO DO DATABASE BRONZE!")

TABELA CIDADE CARREGADA COM SUCESSO DO DATABASE BRONZE!


In [0]:
##  1- Tratamento do campo LOCATION na tabela Conflito - Removento acentos

acento = 'áàãâéèêíìóòôõúùû'
sem_acento = 'aaaaeeeiioooouuu'
df_conflito2 = df_conflito_bronze_sql.withColumn('LOCATION_2', upper(translate(df_conflito_bronze_sql['LOCATION'], acento, sem_acento)))

df_conflito3 = df_conflito2.withColumn('LOCATION_3', when(col('LOCATION_2').like ('%RIO DE JANEIRO%'), 'RIO DE JANEIRO').otherwise(col('LOCATION_2')))

df_conflito4 = df_conflito3.withColumn('ID_CITY', when(col('LOCATION_3').like ('%SAO PAULO%'), 'SAO PAULO').otherwise(col('LOCATION_3')))

#df_conflito4.display()

In [0]:
# 2- Tratamento do campo EVENT_DATE na tabela Conflito - Transformando em mês e ano

split_cols = split(df_conflito4['EVENT_DATE'], '-')
df_conflito4 = df_conflito4.withColumn('EVENT_MONTH', split_cols.getItem(1))
df_conflito4 = df_conflito4.withColumn('EVENT_YEAR', split_cols.getItem(2))

df_conflito4 = df_conflito4.replace(['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'], ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12'])

df_conflito4 = df_conflito4.withColumn('EVENT_MONTH', df_conflito4['EVENT_MONTH'].cast(IntegerType()))
df_conflito4 = df_conflito4.withColumn('EVENT_YEAR', df_conflito4['EVENT_YEAR'].cast(IntegerType()))

#display(df_conflito5)

In [0]:
#  3- Tratamento do campo CITY na tabela Cidade - Removento acentos

acento = 'áàãâéèêíìóòôõúùû'
sem_acento = 'aaaaeeeiioooouuu'
df_cidade2 = df_cidade_bronze_sql.withColumn('ID_CITY', upper(translate(df_cidade_bronze_sql['CITY'], acento, sem_acento)))

#print(df_cidade2.columns)
#print(df_conflito4.columns)

In [0]:
# 4 - Limpeza e transformação dos dados: tradução, eliminação de colunas, rename de colunas

lista_conflito = ['EVENT_DATE','LOCATION','LATITUDE','LONGITUDE','LOCATION_2','LOCATION_3']
df_conflito4 = df_conflito4.drop(*lista_conflito)

df_conflito4 = df_conflito4\
  .withColumnRenamed('EVENT_TYPE', 'TIPO_EVENTO')\
  .withColumnRenamed('SUB_EVENT_TYPE', 'SUB_TIPO_EVENTO')\
  .withColumnRenamed('ACTOR1', 'ATOR_PRIMARIO')\
  .withColumnRenamed('ACTOR2', 'ATOR_SECUNDARIO')\
  .withColumnRenamed('COUNTRY', 'PAIS')\
  .withColumnRenamed('SOURCE_SCALE', 'ESCALA_GEOGRAFICA')\
  .withColumnRenamed('NOTES', 'DESCRICAO')\
  .withColumnRenamed('FATALITIES', 'FATALIDADE')\
  .withColumnRenamed('EVENT_MONTH', 'MES')\
  .withColumnRenamed('EVENT_YEAR', 'ANO')

df_conflito4 = df_conflito4.withColumn('FATALIDADE', df_conflito4['FATALIDADE'].cast(IntegerType()))

#print(df_conflito4.columns)

lista_cidade = ['CITY', 'IBGE_RES_POP', 'IBGE_RES_POP_BRAS', 'IBGE_RES_POP_ESTR', 'IBGE_DU', 'IBGE_DU_URBAN', 'IBGE_DU_RURAL', 'IBGE_POP', 'IBGE_1', 'IBGE_1-4', 'IBGE_5-9', 'IBGE_10-14', 'IBGE_15-59', 'IBGE_60+', 'IBGE_PLANTED_AREA', 'IBGE_CROP_PRODUCTION_$', 'IDHM_Ranking_2010', 'IDHM', 'IDHM_Renda', 'IDHM_Longevidade', 'IDHM_Educacao', 'LONG', 'LAT', 'ALT', 'PAY_TV', 'FIXED_PHONES', 'AREA', 'REGIAO_TUR', 'CATEGORIA_TUR', 'ESTIMATED_POP', 'RURAL_URBAN', 'GVA_AGROPEC', 'GVA_INDUSTRY', 'GVA_SERVICES', 'GVA_PUBLIC', 'GVA_TOTAL', 'TAXES', 'GDP', 'POP_GDP', 'GDP_CAPITA', 'GVA_MAIN', 'MUN_EXPENDIT', 'COMP_TOT', 'COMP_A', 'COMP_B', 'COMP_C', 'COMP_D', 'COMP_E', 'COMP_F', 'COMP_G', 'COMP_H', 'COMP_I', 'COMP_J', 'COMP_K', 'COMP_L', 'COMP_M', 'COMP_N', 'COMP_O', 'COMP_P', 'COMP_Q', 'COMP_R', 'COMP_S', 'COMP_T', 'COMP_U', 'HOTELS', 'BEDS', 'Pr_Agencies', 'Pu_Agencies', 'Pr_Bank', 'Pu_Bank', 'Pr_Assets', 'Pu_Assets', 'Cars', 'Motorcycles', 'Wheeled_tractor', 'UBER', 'MAC', 'WAL-MART', 'POST_OFFICES']
df_cidade2 = df_cidade2.drop(*lista_cidade)

df_cidade2 = df_cidade2\
  .withColumnRenamed('STATE', 'ESTADO')\

#print(df_cidade2.columns)



In [0]:
%sql
CREATE DATABASE IF NOT EXISTS silver

In [0]:
print("DATABASE SILVER CRIADO COM SUCESSO!")

DATABASE SILVER CRIADO COM SUCESSO!


In [0]:
%sql
DROP TABLE IF EXISTS silver.conflito

In [0]:
%sql
DROP TABLE IF EXISTS silver.cidade

In [0]:
# 5- Criação do DATABASE Silver e Carga das tabelas Conflito e Cidade

dbutils.fs.rm('dbfs:/user/hive/warehouse/silver.db/conflito',True)

df_conflito4.write.format("delta").mode("append").saveAsTable("silver.conflito")

print("CARGA DADOS DE CONFLITO CRIADO COM SUCESSO NO DATABASE SILVER!")

dbutils.fs.rm('dbfs:/user/hive/warehouse/silver.db/cidade',True)

df_cidade2.write.format("delta").mode("append").saveAsTable("silver.cidade")

print("CARGA DADOS DE CIDADE CRIADO COM SUCESSO NO DATABASE SILVER!")

CARGA DADOS DE CONFLITO CRIADO COM SUCESSO NO DATABASE SILVER!
CARGA DADOS DE CIDADE CRIADO COM SUCESSO NO DATABASE SILVER!


In [0]:
display(df_conflito4)

display(df_cidade2)

TIPO_EVENTO SUB_TIPO_EVENTO ATOR_PRIMARIO ATOR_SECUNDARIO PAIS ESCALA_GEOGRAFICA DESCRICAO FATALIDADE ID_CITY MES ANO Battles Armed clash Unidentified Gang and/or Police Militia Military Forces of Brazil (2016-2018) Military Police Brazil Subnational On 23 June 2018, in Viamao, Rio Grande do Sul, the military police tried to approach a suspicious car and an armed clash took place between police officers and these armed men in the car in the Mario Quintana neighborhood. Two suspects were injured and all three were arrested. The Police seized a revolver and a pistol. 0 VIAMAO 6 2018 Explosions/Remote violence Remote explosive/landmine/IED Unidentified Gang (Brazil) null Brazil Subnational On 23 June 2018, in Caldas Novas, Goias, a bank was blown up by at least five armed individuals. Three suspects were arrested. 0 CALDAS NOVAS 6 2018 Battles Armed clash Unidentified Gang and/or Police Militia Unidentified Gang (Brazil) Brazil National On 23 June 2018, in Teresina, Piaui, a man was killed and another was injured by armed men on a motorcycle in Parque Brasil II neighborhood. Both victims were involved in drug trafficking activities and the motivation for the attack would have been a settlement of scores. 1 TERESINA 6 2018 Violence against civilians Attack Unidentified Gang and/or Police Militia Civilians (Brazil) Brazil National On 23 June 2018, in Santo Andre, Sao Paulo, a man was killed and his body was dismembered and abandoned in a wheelbarrow in Vila Homero Thon neighbourhood. Two suspects were arrested. 1 SANTO ANDRE 6 2018 Strategic developments Looting/property destruction Police Forces of Brazil (2016-2018) Federal Police Unidentified Gang (Brazil) Brazil National On 23 June 2018, in Borborema, Sao Paulo, 1,4 tones of cocaine were seized by the Federal Highway Police on km 458 of the BR-245 highway. 0 BORBOREMA 6 2018 Battles Armed clash Military Forces of Brazil (2016-2018) Military Police Unidentified Gang and/or Police Militia Brazil National-International On 23 June 2018, in Angra dos Reis, Rio de Janeiro, the BOPE military police engaged in a shoot-out with drug traffickers during a security operation in Areal community. Two suspects were killed. The police seized weapons, a grenade, and a radio communicator. 2 fatalities. 2 ANGRA DOS REIS 6 2018 Explosions/Remote violence Remote explosive/landmine/IED Unidentified Gang (Brazil) null Brazil National On 23 June 2018, in Imaculada, Paraiba, a National Postal Service branch was blown up by at least four men. 0 IMACULADA 6 2018 Strategic developments Looting/property destruction Police Forces of Brazil (2016-2018) Federal Police Unidentified Gang (Brazil) Brazil Subnational-National On 23 June 2018, in Ponta Pora, Mato Grosso do Sul, 1.1 tons of marijuana were found inside a vehicle and seized by the Federal Highway Police. On km 68 of the BR-463, over 5.400 tones of marijuana were seized inside a truck by the Federal Police. The truck driver was arrested. 0 PONTA PORA 6 2018 Violence against civilians Attack Unidentified Gang and/or Police Militia Civilians (Brazil) Brazil Subnational Around 23 June 2018 (as reported), in Rio Largo, Alagoas, a woman was killed and her body was found without the head in Mata do Rolo neighborhood. 1 RIO LARGO 6 2018 Battles Armed clash Unidentified Gang (Brazil) Unidentified Gang (Brazil) Brazil National On 23 June 2018, in Coelho Neto, Maranhao, a drug trafficking group invaded the area of a rival drug trafficking group in order to gain territorial control of selling points in Jorge Turco community. During the clash, one civilian bystander was shot and killed. 1 COELHO NETO 6 2018 Battles Armed clash Unidentified Armed Group (Brazil) Unidentified Armed Group (Brazil) Brazil New media On 23 June 2018, in Angra dos Reis, Rio de Janeiro, a shoot-out was reported in Sapinhatuba II neighbourhood. 0 ANGRA DOS REIS 6 2018 Battles Armed clash Unidentified Gang and/or Police Militia Military Forces of Brazil (2016-2018) Military Police Brazil Su

ESTADO CAPITAL ID_CITY GO 0 ABADIA DE GOIAS MG 0 ABADIA DOS DOURADOS GO 0 ABADIANIA PA 0 ABAETETUBA MG 0 ABAETE CE 0 ABAIARA BA 0 ABARE PR 0 ABATIA BA 0 ABAIRA SC 0 ABDON BATISTA PA 0 ABEL FIGUEIREDO SC 0 ABELARDO LUZ MG 0 ABRE CAMPO PE 0 ABREU E LIMA TO 0 ABREULANDIA MG 0 ACAIACA BA 0 ACAJUTIBA CE 0 ACARAPE CE 0 ACARAU RN 0 ACARI PA 0 ACARA PI 0 ACAUA RS 0 ACEGUA CE 0 ACOPIARA MT 0 ACORIZAL AC 0 ACRELANDIA GO 0 ACREUNA SP 0 ADAMANTINA GO 0 ADELANDIA SP 0 ADOLFO PR 0 ADRIANOPOLIS BA 0 ADUSTINA PE 0 AFOGADOS DA INGAZEIRA RN 0 AFONSO BEZERRA ES 0 AFONSO CLAUDIO MA 0 AFONSO CUNHA PE 0 AFRANIO PA 0 AFUA PE 0 AGRESTINA PI 0 AGRICOLANDIA SC 0 AGROLANDIA SC 0 AGRONOMICA MG 0 AGUANIL SP 0 AGUAI RS 0 AGUDO SP 0 AGUDOS PR 0 AGUDOS DO SUL PB 0 AGUIAR TO 0 AGUIARNOPOLIS MG 0 AIMORES BA 0 AIQUARA CE 0 AIUABA MG 0 AIURUOCA RS 0 AJURICABA MG 0 ALAGOA PB 0 ALAGOA GRANDE PB 0 ALAGOA NOVA PE 0 ALAGOINHA PB 0 ALAGOINHA PI 0 ALAGOINHA DO PIAUI BA 0 ALAGOINHAS SP 0 ALAMBARI MG 0 ALBERTINA PB 0 ALCANTIL MS 0 ALCINOPOLIS BA 0 ALCOBAÇA MA 0 ALCANTARA CE 0 ALCANTARAS MA 0 ALDEIAS ALTAS RS 0 ALECRIM ES 0 ALEGRE RS 0 ALEGRETE PI 0 ALEGRETE DO PIAUI RS 0 ALEGRIA PA 0 ALENQUER RN 0 ALEXANDRIA GO 0 ALEXANIA MG 0 ALFENAS ES 0 ALFREDO CHAVES SP 0 ALFREDO MARCONDES MG 0 ALFREDO VASCONCELOS SC 0 ALFREDO WAGNER PB 0 ALGODAO DE JANDAIRA PB 0 ALHANDRA PE 0 ALIANÇA TO 0 ALIANÇA DO TOCANTINS BA 0 ALMADINA TO 0 ALMAS PA 0 ALMEIRIM MG 0 ALMENARA RN 0 ALMINO AFONSO PR 0 ALMIRANTE TAMANDARE RS 0 ALMIRANTE TAMANDARE DO SUL GO 0 ALOANDIA MG 0 ALPERCATA RS 0 ALPESTRE MG 0 ALPINOPOLIS MT 0 ALTA FLORESTA RO 0 ALTA FLORESTA D'OESTE SP 0 ALTAIR PA 0 ALTAMIRA MA 0 ALTAMIRA DO MARANHAO PR 0 ALTAMIRA DO PARANA CE 0 ALTANEIRA MG 0 ALTEROSA PE 0 ALTINHO SP 0 ALTINOPOLIS SP 0 ALTO ALEGRE RR 0 ALTO ALEGRE RS 0 ALTO ALEGRE MA 0 ALTO ALEGRE DO MARANHAO MA 0 ALTO ALEGRE DO PINDARE RO 0 ALTO ALEGRE DOS PARECIS MT 0 ALTO ARAGUAIA SC 0 ALTO BELA VISTA MT 0 ALTO BOA VISTA MG 0 ALTO CAPARAO RN 0 ALTO DO RODRIGUES RS 0 ALTO FELIZ MT 0 ALTO GARÇAS GO 0 ALTO HORIZONTE MG 0 ALTO JEQUITIBA PI 0 ALTO LONGA MT 0 ALTO PARAGUAI PR 0 ALTO PARANA RO 0 ALTO PARAISO PR 0 ALTO PARAISO GO 0 ALTO PARAISO DE GOIAS MA 0 ALTO PARNAIBA PR 0 ALTO PIQUIRI MG 0 ALTO RIO DOCE ES 0 ALTO RIO NOVO CE 0 ALTO SANTO MT 0 ALTO TAQUARI PI 0 ALTOS PR 0 ALTONIA SP 0 ALUMINIO MG 0 ALVARENGA AM 0 ALVARAES SP 0 ALVINLANDIA MG 0 ALVINOPOLIS TO 0 ALVORADA RS 0 ALVORADA RO 0 ALVORADA D'OESTE MG 0 ALVORADA DE MINAS PI 0 ALVORADA DO GURGUEIA GO 0 ALVORADA DO NORTE PR 0 ALVORADA DO SUL MG 0 ALEM PARAIBA RR 0 AMAJARI MS 0 AMAMBAI PR 0 AMAPORA AP 0 AMAPA MA 0 AMAPA DO MARANHAO PE 0 AMARAJI RS 0 AMARAL FERRADOR GO 0 AMARALINA PI 0 AMARANTE MA 0 AMARANTE DO MARANHAO BA 0 AMARGOSA AM 0 AMATURA SP 0 AMERICANA GO 0 AMERICANO DO BRASIL RS 0 AMETISTA DO SUL CE 0 AMONTADA GO 0 AMORINOPOLIS SP 0 AMPARO PB 0 AMPARO SE 0 AMPARO DE SAO FRANCISCO MG 0 AMPARO DO SERRA PR 0 AMPERE BA 0 AMELIA RODRIGUES BA 0 AMERICA DOURADA SP 0 AMERICO BRASILIENSE SP 0 AMERICO DE CAMPOS AL 0 ANADIA BA 0 ANAGE PR 0 ANAHY MA 0 ANAJATUBA PA 0 ANAJAS SP 0 ANALANDIA AM 0 ANAMA PA 0 ANANINDEUA TO 0 ANANAS PA 0 ANAPU MA 0 ANAPURUS MS 0 ANASTACIO MS 0 ANAURILANDIA ES 0 ANCHIETA SC 0 ANCHIETA BA 0 ANDARAI PR 0 ANDIRA BA 0 ANDORINHA MG 0 ANDRADAS SP 0 ANDRADINA MG 0 ANDRELANDIA RS 0 ANDRE DA ROCHA SP 0 ANGATUBA PE 0 ANGELIM SC 0 ANGELINA MG 0 ANGELANDIA BA 0 ANGICAL PI 0 ANGICAL DO PIAUI TO 0 ANGICO RN 0 ANGICOS RJ 0 ANGRA DOS REIS BA 0 ANGUERA MS 0 ANGELICA GO 0 ANHANGUERA SP 0 ANHEMBI SP 0 ANHUMAS GO 0 ANICUNS SC 0 ANITA GARIBALDI SC 0 ANITAPOLIS AM 0 ANORI RS 0 ANTA GORDA BA 0 ANTAS PR 0 ANTONINA CE 0 ANTONINA DO NORTE PI 0 ANTONIO ALMEIDA BA 0 ANTONIO CARDOSO SC 0 ANTONIO CARLOS MG 0 ANTONIO CARLOS MG 0 ANTONIO DIAS BA 0 ANTONIO GONÇALVES MS 0 ANTONIO JOAO RN 0 ANTONIO MARTINS PR 0 ANTONIO OLINTO RS 0 ANTONIO PRADO MG 0 ANTONIO PRADO DE MINAS GO 0 ANAPOLIS PI 0 ANISIO DE ABREU SP 0 APARECIDA PB 0 APARECIDA SP 0 APARECIDA D'OESTE GO 0 APARECIDA DE GOIANIA GO 0 APARECIDA DO